In [1]:
import sys
from pathlib import Path
from os import chdir

project_directory = Path('../..').resolve()
sys.path.extend(['../..'])

In [2]:
from os import getcwd, path
import plotly.express as px
from environs import Env

In [16]:
from internal.feature_analysis.compile_epochs import compile_epochs
from internal.feature_analysis.index_character_epochs import \
    index_character_epochs, \
    flatten_character_index
from internal.feature_analysis.list_relevant_file import list_relevant_files
from internal.feature_analysis.reduce_dimensions import reduce_dimensions
from src.pkg.config_constants import \
    PCA_COMPONENTS, \
    INPUT
from src.pkg.get_output_dir import get_output_dir
from src.pkg.load_config import load_config
from src.pkg.load_env import load_env

In [17]:
PATH = 'PATH'
MIME = 'MIME'

In [18]:
def get_pca_dimensions(env: Env) -> int:
    return env.int(PCA_COMPONENTS)

In [19]:
def get_input(config: dict) -> (str, str):
    _input = config[INPUT]
    return _input[PATH], _input[MIME]

In [20]:
cwd = getcwd()
process_dir = cwd

In [21]:
env = load_env(process_dir)
config = load_config(process_dir, env)
pca_dimensions = get_pca_dimensions(env)
path_name, mime = get_input(config)

In [22]:
from src.pkg.index_epochs import index_epochs
from src.pkg.config_constants import \
    FILE_META_EXTRACTOR_REGEX, \
    FILE_NAME_TEMPLATE_CHARACTER_PARTIAL

In [23]:
meta = list_relevant_files(project_directory, mime, path.join(project_directory, path_name))
epochs = compile_epochs(meta)

In [24]:
indexed = index_character_epochs(epochs)
reduced = reduce_dimensions(pca_dimensions, indexed)
flattened = flatten_character_index(reduced)

In [25]:
flattened

character         x         y         z
epoch                                        
0             2  0.390277  1.461398  0.188958
1             2  0.358528  1.322745  0.559853
2             2  1.191124 -1.174554  0.296664
3             2 -1.249717 -0.921876  0.808871
4             2  0.001162 -1.617088 -0.476274
...         ...       ...       ...       ...
4132          6  0.774352  0.826698  0.374498
4133          6  1.036252  0.590604  0.671511
4134          6  0.418386  0.502794  1.279178
4135          6  0.463668  0.743744  0.915471
4136          6  1.229947  0.538235 -0.276767

[42000 rows x 4 columns]

In [31]:
fig = px.scatter_3d(
    flattened,
    x='x',
    y='y',
    z='z',
    color='character',
    height=900,
    width=900,
)
fig.show()